In [1]:
import numpy as np
import pandas as pd
import os
import glob

import mne
from mne.time_frequency import psd_array_multitaper
from scipy.integrate import simps
from yasa import sliding_window
from lazypredict.Supervised import LazyClassifier

/home/shivam/anaconda3/lib/python3.9/site-packages/outdated/utils.py:14: OutdatedPackageWarning: The package outdated is out of date. Your version is 0.2.1, the latest is 0.2.2.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  return warn(
/home/shivam/anaconda3/lib/python3.9/site-packages/outdated/utils.py:14: OutdatedPackageWarning: The package yasa is out of date. Your version is 0.6.1, the latest is 0.6.3.
Set the environment variable OUTDATED_IGNORE=1 to disable these warnings.
  return warn(


In [2]:
data_path = "/mnt/sda1/shivam/Thesis/Grasp Experiment/Data/PreprocessedData/Preprocess HAPPE"
exclusion = ["FP01.set", "FP10.set"]
os.chdir(data_path)

In [3]:
sf = 1000
ch_type = "eeg"
nchan = 64
channels = [f'E{n:1}' for n in range(1, nchan+1)]

In [4]:
mne.channels.get_builtin_montages()
chans = mne.channels.make_standard_montage('GSN-HydroCel-64_1.0')
info = mne.create_info(channels, sfreq=sf, ch_types=ch_type)
info.set_montage(chans)

<Info | 8 non-empty values
 bads: []
 ch_names: E1, E2, E3, E4, E5, E6, E7, E8, E9, E10, E11, E12, E13, E14, ...
 chs: 64 EEG
 custom_ref_applied: False
 dig: 67 items (3 Cardinal, 64 EEG)
 highpass: 0.0 Hz
 lowpass: 500.0 Hz
 meas_date: unspecified
 nchan: 64
 projs: []
 sfreq: 1000.0 Hz
>

In [5]:
def get_action_events(events):
    new_keys_dict = {}
    for key in events[1].keys():
        if "ActionBeg" in key:
            new_keys_dict[key] = events[1][key]
        if "FixBeg" in key and "Free" not in key:
            new_keys_dict[key] = events[1][key]
    
    new_event_times = [row for row in events[0] if row[2] in new_keys_dict.values()] 
    return (new_event_times, new_keys_dict)

In [7]:
eeg_df_main = pd.DataFrame()

for files in glob.glob("*.set"):
    if files not in exclusion:
        print("#############")
        print(files)
        # Read EEG and event file
        arr = mne.io.read_raw_eeglab(files, verbose=0)
        eeg_data = arr.to_data_frame()
        events = mne.events_from_annotations(arr, verbose=0)

        # Extracting events of interest
        new_events = get_action_events(events)

        # Working with epochs
        epochs = mne.Epochs(
            arr, new_events[0], event_id=new_events[1], tmin=0, tmax=0.999,  baseline=None, verbose=0
        )
        epoch_df = epochs.to_data_frame()
        # Here epoch ~ trial
        n_epochs = len(np.unique(epoch_df['epoch']))
        
        all_epochs_df = pd.DataFrame()
        ctr = 0
        for epoch in range(n_epochs):
            epoch_eeg = epoch_df[epoch_df["epoch"] == epoch]
            label = epoch_eeg.condition.iloc[0] 
            eeg_data = epoch_eeg.reset_index().iloc[:, 4:].T
            
            eeg_data["Event"] = label.split("-")[0][:-3]
            eeg_data["HandPos"] = label.split("-")[1]
            eeg_data["Hand"] = label.split("-")[2]
            eeg_data["Action"] = label.split("-")[3]
            eeg_data["Subject"] = files.split(".")[0]
            eeg_data["Channel"] = [x[1:] for x in eeg_data.index]
            eeg_data["Trial"] = ctr
            
            ctr += 1
            
            eeg_data = eeg_data.reset_index()
            all_epochs_df = pd.concat([all_epochs_df, eeg_data])

        eeg_df_main = pd.concat([eeg_df_main, all_epochs_df])
        print(eeg_df_main.shape)
        print(np.unique(eeg_df_main.Event, return_counts=True))

#############
P01.set
Using data from preloaded Raw for 960 events and 1000 original time points ...
0 bad epochs dropped
(61440, 1008)
(array(['Action', 'Fix'], dtype=object), array([30720, 30720]))
#############
P03.set
Using data from preloaded Raw for 960 events and 1000 original time points ...
0 bad epochs dropped
(117120, 1008)
(array(['Action', 'Fix'], dtype=object), array([58560, 58560]))
#############
FP03.set
Using data from preloaded Raw for 960 events and 1000 original time points ...
0 bad epochs dropped
(175680, 1008)
(array(['Action', 'Fix'], dtype=object), array([87840, 87840]))
#############
FP05.set
Using data from preloaded Raw for 960 events and 1000 original time points ...
0 bad epochs dropped
(236160, 1008)
(array(['Action', 'Fix'], dtype=object), array([118080, 118080]))
#############
FP09.set
Using data from preloaded Raw for 960 events and 1000 original time points ...
0 bad epochs dropped
(296640, 1008)
(array(['Action', 'Fix'], dtype=object), array([148320,

In [8]:
eeg_df_main

index     0     1     2     3     4     5     6     7     8  ...    997  \
0     E1 -6.92 -7.04 -7.18 -7.35 -7.52 -7.69 -7.85 -7.98 -8.07  ...  -9.20   
1     E2 -7.83 -7.64 -7.46 -7.27 -7.09 -6.90 -6.71 -6.52 -6.32  ...  -0.10   
2     E3 -7.87 -7.54 -7.17 -6.76 -6.32 -5.87 -5.41 -4.96 -4.53  ...  -2.77   
3     E4 -1.14 -0.93 -0.75 -0.61 -0.51 -0.45 -0.43 -0.44 -0.48  ...  -4.28   
4     E5 -8.30 -8.16 -7.96 -7.71 -7.40 -7.05 -6.65 -6.23 -5.78  ...   8.10   
..   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...    ...   
57   E58  8.82  8.21  7.50  6.72  5.91  5.08  4.27  3.50  2.80  ... -10.10   
58   E59 12.37 11.62 10.73  9.72  8.63  7.49  6.32  5.17  4.05  ... -18.79   
59   E60  6.91  6.91  6.89  6.86  6.82  6.75  6.65  6.51  6.31  ...  -8.47   
60   E61  4.53  4.61  4.67  4.71  4.75  4.78  4.82  4.87  4.93  ...  -5.12   
61   E62  0.29  0.19  0.11  0.07  0.08  0.14  0.25  0.43  0.66  ...  -4.09   

      998    999   Event   HandPos   Hand  Action  Subject  Channel  Trial  
0   -9.17  -9.16     Fix  palmDown  Right    Open      P01        1      0  
1   -0.29  -0.48     Fix  palmDown  Right    Open      P01        2      0  
2   -2.62  -2.52     Fix  palmDown  Right    Open      P01        3      0  
3   -3.89  -3.55     Fix  palmDown  Right    Open      P01        4      0  
4    7.97   7.78     Fix  palmDown  Right    Open      P01        5      0  
..    ...    ...     ...       ...    ...     ...      ...      ...    ...  
57 -10.29 -10.18  Action    palmUp  Right   Close     FP12       58    959  
58 -18.98 -18.81  Action    palmUp  Right   Close     FP12       59    959  
59  -7.65  -6.60  Action    palmUp  Right   Close     FP12       60    959  
60  -5.36  -5.53  Action    palmUp  Right   Close     FP12       61    959  
61  -4.59  -5.12  Action    palmUp  Right   Close     FP12       62    959  

[769920 rows x 1008 columns]

In [9]:
df = pd.DataFrame(eeg_df_main, columns=list(range(1000))+["Event", "HandPos", "Hand", "Action", "Subject", "Channel", "Trial"])
os.chdir("/mnt/sda1/shivam/Thesis/Grasp Experiment/Data/CleanSep/")
df.to_csv("cleaned_data_asr_fix_v1.csv", index=False, header=list(range(1000))+["Event", "handPos", "Hand", "Action", "Subject", "Channel", "Trial"])
df

0     1     2     3     4     5     6     7     8     9  ...    997  \
0  -6.92 -7.04 -7.18 -7.35 -7.52 -7.69 -7.85 -7.98 -8.07 -8.12  ...  -9.20   
1  -7.83 -7.64 -7.46 -7.27 -7.09 -6.90 -6.71 -6.52 -6.32 -6.12  ...  -0.10   
2  -7.87 -7.54 -7.17 -6.76 -6.32 -5.87 -5.41 -4.96 -4.53 -4.13  ...  -2.77   
3  -1.14 -0.93 -0.75 -0.61 -0.51 -0.45 -0.43 -0.44 -0.48 -0.56  ...  -4.28   
4  -8.30 -8.16 -7.96 -7.71 -7.40 -7.05 -6.65 -6.23 -5.78 -5.31  ...   8.10   
..   ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...    ...   
57  8.82  8.21  7.50  6.72  5.91  5.08  4.27  3.50  2.80  2.19  ... -10.10   
58 12.37 11.62 10.73  9.72  8.63  7.49  6.32  5.17  4.05  3.01  ... -18.79   
59  6.91  6.91  6.89  6.86  6.82  6.75  6.65  6.51  6.31  6.05  ...  -8.47   
60  4.53  4.61  4.67  4.71  4.75  4.78  4.82  4.87  4.93  5.00  ...  -5.12   
61  0.29  0.19  0.11  0.07  0.08  0.14  0.25  0.43  0.66  0.95  ...  -4.09   

      998    999   Event   HandPos   Hand  Action  Subject  Channel  Trial  
0   -9.17  -9.16     Fix  palmDown  Right    Open      P01        1      0  
1   -0.29  -0.48     Fix  palmDown  Right    Open      P01        2      0  
2   -2.62  -2.52     Fix  palmDown  Right    Open      P01        3      0  
3   -3.89  -3.55     Fix  palmDown  Right    Open      P01        4      0  
4    7.97   7.78     Fix  palmDown  Right    Open      P01        5      0  
..    ...    ...     ...       ...    ...     ...      ...      ...    ...  
57 -10.29 -10.18  Action    palmUp  Right   Close     FP12       58    959  
58 -18.98 -18.81  Action    palmUp  Right   Close     FP12       59    959  
59  -7.65  -6.60  Action    palmUp  Right   Close     FP12       60    959  
60  -5.36  -5.53  Action    palmUp  Right   Close     FP12       61    959  
61  -4.59  -5.12  Action    palmUp  Right   Close     FP12       62    959  

[769920 rows x 1007 columns]

In [10]:
np.unique(df.Event, return_counts=True)

(array(['Action', 'Fix'], dtype=object), array([384960, 384960]))

# Calculating Power Spectral Density for Fix and Action

In [5]:
os.chdir("/mnt/sda1/shivam/Thesis/Grasp Experiment/Data/CleanSep/")
dataset = pd.read_csv("cleaned_data_asr_fix_v1.csv")
dataset

0     1     2     3     4     5     6     7     8     9  ...  \
0      -6.92 -7.04 -7.18 -7.35 -7.52 -7.69 -7.85 -7.98 -8.07 -8.12  ...   
1      -7.83 -7.64 -7.46 -7.27 -7.09 -6.90 -6.71 -6.52 -6.32 -6.12  ...   
2      -7.87 -7.54 -7.17 -6.76 -6.32 -5.87 -5.41 -4.96 -4.53 -4.13  ...   
3      -1.14 -0.93 -0.75 -0.61 -0.51 -0.45 -0.43 -0.44 -0.48 -0.56  ...   
4      -8.30 -8.16 -7.96 -7.71 -7.40 -7.05 -6.65 -6.23 -5.78 -5.31  ...   
...      ...   ...   ...   ...   ...   ...   ...   ...   ...   ...  ...   
769915  8.82  8.21  7.50  6.72  5.91  5.08  4.27  3.50  2.80  2.19  ...   
769916 12.37 11.62 10.73  9.72  8.63  7.49  6.32  5.17  4.05  3.01  ...   
769917  6.91  6.91  6.89  6.86  6.82  6.75  6.65  6.51  6.31  6.05  ...   
769918  4.53  4.61  4.67  4.71  4.75  4.78  4.82  4.87  4.93  5.00  ...   
769919  0.29  0.19  0.11  0.07  0.08  0.14  0.25  0.43  0.66  0.95  ...   

          997    998    999   Event   handPos   Hand  Action  Subject  \
0       -9.20  -9.17  -9.16     Fix  palmDown  Right    Open      P01   
1       -0.10  -0.29  -0.48     Fix  palmDown  Right    Open      P01   
2       -2.77  -2.62  -2.52     Fix  palmDown  Right    Open      P01   
3       -4.28  -3.89  -3.55     Fix  palmDown  Right    Open      P01   
4        8.10   7.97   7.78     Fix  palmDown  Right    Open      P01   
...       ...    ...    ...     ...       ...    ...     ...      ...   
769915 -10.10 -10.29 -10.18  Action    palmUp  Right   Close     FP12   
769916 -18.79 -18.98 -18.81  Action    palmUp  Right   Close     FP12   
769917  -8.47  -7.65  -6.60  Action    palmUp  Right   Close     FP12   
769918  -5.12  -5.36  -5.53  Action    palmUp  Right   Close     FP12   
769919  -4.09  -4.59  -5.12  Action    palmUp  Right   Close     FP12   

        Channel  Trial  
0             1      0  
1             2      0  
2             3      0  
3             4      0  
4             5      0  
...         ...    ...  
769915       58    959  
769916       59    959  
769917       60    959  
769918       61    959  
769919       62    959  

[769920 rows x 1007 columns]

In [6]:
np.unique(dataset.Trial)

array([  0,   1,   2,   3,   4,   5,   6,   7,   8,   9,  10,  11,  12,
        13,  14,  15,  16,  17,  18,  19,  20,  21,  22,  23,  24,  25,
        26,  27,  28,  29,  30,  31,  32,  33,  34,  35,  36,  37,  38,
        39,  40,  41,  42,  43,  44,  45,  46,  47,  48,  49,  50,  51,
        52,  53,  54,  55,  56,  57,  58,  59,  60,  61,  62,  63,  64,
        65,  66,  67,  68,  69,  70,  71,  72,  73,  74,  75,  76,  77,
        78,  79,  80,  81,  82,  83,  84,  85,  86,  87,  88,  89,  90,
        91,  92,  93,  94,  95,  96,  97,  98,  99, 100, 101, 102, 103,
       104, 105, 106, 107, 108, 109, 110, 111, 112, 113, 114, 115, 116,
       117, 118, 119, 120, 121, 122, 123, 124, 125, 126, 127, 128, 129,
       130, 131, 132, 133, 134, 135, 136, 137, 138, 139, 140, 141, 142,
       143, 144, 145, 146, 147, 148, 149, 150, 151, 152, 153, 154, 155,
       156, 157, 158, 159, 160, 161, 162, 163, 164, 165, 166, 167, 168,
       169, 170, 171, 172, 173, 174, 175, 176, 177, 178, 179, 18

In [7]:
subjects = np.unique(dataset.Subject)
X, y_oc, y_lr, y_pos, subjs, y_event = [], [], [], [], [], []
grasp_labels = {"Open": 0, "Close": 1}
hand_labels = {"Left": 0, "Right": 1}
pos_dict = {"palmDown": 0, "palmUp": 1, "palmIn": 2}
event_dict = {"Action": 0, "Fix": 1}

for sub in subjects:
    sub_channels = np.unique(dataset[dataset["Subject"] == sub].iloc[:, -2])
    for palm in ["palmDown", "palmIn", "palmUp"]:
        for oc in ["Open", "Close"]:
            for hand in ["Left", "Right"]:
                cond_data = dataset[(dataset["handPos"] == palm) & 
                        (dataset["Action"] == oc) & 
                        (dataset["Hand"] == hand) & 
                        (dataset["Subject"] == sub)]
                epochs = np.unique(cond_data.iloc[:, -1])                
                
                for i in epochs:
                    test_sub_trial = cond_data[cond_data["Trial"] == i]
                    test_sub_trial.index = test_sub_trial.iloc[:, -2]
                     
                    X.append(test_sub_trial.iloc[:, :-6].to_numpy())
                    subjs.append(test_sub_trial.iloc[0, -3])
                    y_oc.append(grasp_labels[test_sub_trial.iloc[0, -4]])
                    y_lr.append(hand_labels[test_sub_trial.iloc[0, -5]])
                    y_pos.append(pos_dict[test_sub_trial.iloc[0, -6]])
                    y_event.append(event_dict[test_sub_trial.iloc[0, -7]])

X = np.array(X)
y_oc = np.array(y_oc) 
y_lr = np.array(y_lr)
y_pos = np.array(y_pos) 
subjs = np.array(subjs)
y_event = np.array(y_event)
X.shape, y_oc.shape, y_lr.shape, y_pos.shape, subjs.shape, y_event.shape

((12480,), (12480,), (12480,), (12480,), (12480,), (12480,))

In [11]:
# Multitaper method
def bandpower_multitaper(data, sf, method, band, relative=False):
    band = np.asarray(band)
    low, high = band

    if method == 'multitaper':
        psd_trial, freqs = psd_array_multitaper(data, sf, adaptive=True, n_jobs=20,
                                                normalization='full', verbose=False)
    # Frequency resolution
    freq_res = freqs[1] - freqs[0]

    # Find index of band in frequency vector
    idx_band = np.logical_and(freqs >= low, freqs <= high)

    # Integral approximation of the spectrum using parabola (Simpson's rule)
    bp = simps(psd_trial[idx_band], dx=freq_res)

    return bp

In [12]:
def create_bandpower_features(epochs, frequency):
    bandpower_multitaper_EEG = []
    # Iterating over each subject 
    for epoch in epochs:
        # Iterating over each song per subject [30]
        bands_video = []
        no_channels = epoch.shape[0]
        input_brainwaves = epoch
        # Iterating over each channel [14]
        for k in range(no_channels):
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[0.5, 4], relative=False))
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[4, 7], relative=False))
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[8, 13], relative=False))
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[14, 30], relative=False))
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[31, 50], relative=False))
            bands_video.append(bandpower_multitaper(input_brainwaves[k,:], sf=frequency, method='multitaper',
                                                    band=[8, 40], relative=False))
      
        bandpower_multitaper_EEG.append(bands_video)

    bandpower_multitaper_EEG = np.array(bandpower_multitaper_EEG)

    return bandpower_multitaper_EEG

In [ ]:
sf = 1000
window = 1
psd_features = []
for x in X:
    epochs = sliding_window(x, sf=sf, window=window, step=window)[1]
    psd = create_bandpower_features(epochs, sf)
    psd_features.append(psd)
    print(len(psd_features))
psd_features = np.array(psd_features)
psd_features.shape

/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative mult

1


/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative mult

2


/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative mult

...

8463
8464
8465
8466
8467
8468
8469
8470


/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative mult

8471
8472


/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative multi-taper PSD computation did not converge.
  return [func(*args, **kwargs)
/home/shivam/anaconda3/lib/python3.9/site-packages/joblib/parallel.py:262: RuntimeWarning: Iterative mult

8473


In [ ]:
# Out of 12480

In [1]:
X.shape, y_oc.shape, y_lr.shape, y_pos.shape, subjs.shape, y_event.shape

NameError: name 'X' is not defined

In [ ]:
os.chdir("/mnt/sda1/shivam/Thesis/Grasp Experiment/Data/IntData/ASR v2/")
np.save("psd_label_lr.npy", y_lr)
np.save("psd_label_pos.npy", y_pos)
np.save("psd_label_oc.npy", y_oc)
np.save("psd_label_subj.npy", subjs)
np.save("psd_label_event.npy", y_event)

In [ ]:
pd.DataFrame(psd_features).to_csv("psd_features_v2.csv")